In [ ]:
#
# Copyright 2021- IBM Inc. All rights reserved
# SPDX-License-Identifier: Apache2.0
#

In [1]:
import tensorflow as tf
from tensorflow import keras
import numpy as np
import pandas as pd
import math
import os
import joblib
import pydot
print(tf.__version__)

2.11.0


In [2]:
seq_length = 7 # Six past transactions followed by current transaction

# Process database

In [3]:
tdf = pd.read_csv('Data/card_transaction.v1.csv')
tdf['Merchant Name'] = tdf['Merchant Name'].astype(str)
tdf.sort_values(by=['User','Card'], inplace=True)
tdf.reset_index(inplace=True, drop=True)
print (tdf.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 24386900 entries, 0 to 24386899
Data columns (total 15 columns):
 #   Column          Dtype  
---  ------          -----  
 0   User            int64  
 1   Card            int64  
 2   Year            int64  
 3   Month           int64  
 4   Day             int64  
 5   Time            object 
 6   Amount          object 
 7   Use Chip        object 
 8   Merchant Name   object 
 9   Merchant City   object 
 10  Merchant State  object 
 11  Zip             float64
 12  MCC             int64  
 13  Errors?         object 
 14  Is Fraud?       object 
dtypes: float64(1), int64(6), object(8)
memory usage: 2.7+ GB
None


In [4]:
# Get first of each User-Card combination
first = tdf[['User','Card']].drop_duplicates()
f = np.array(first.index)

In [6]:
# Drop the first N transactions
drop_list = np.concatenate([np.arange(x,x + seq_length - 1) for x in f])
index_list = np.setdiff1d(tdf.index.values,drop_list)

In [7]:
# Split into 0.5 train, 0.3 validate, 0.2 test
tot_length = index_list.shape[0]
train_length = tot_length // 2
validate_length = (tot_length - train_length) * 3 // 5
test_length = tot_length - train_length - validate_length
print (tot_length,train_length,validate_length, test_length)

24350099 12175049 7305030 4870020


In [8]:
# Generate list of indices for train, validate, test
np.random.seed(1111)
train_indices = np.random.choice(index_list, train_length, replace=False)
tv_list = np.setdiff1d(index_list, train_indices)
validate_indices = np.random.choice(tv_list, validate_length, replace=False)
test_indices = np.setdiff1d(tv_list, validate_indices)
print (train_indices, validate_indices, test_indices)

[ 9802207 14106565  3424650 ...   986295    31770 22457273] [11386714 20819702 13959897 ...  6750280  4076771 23370874] [       9       14       23 ... 24386880 24386886 24386894]


# Uncomment the last line to generate a test sample: database + test indices

In [9]:
def create_test_sample(df, indices):
    print(indices)
    rows = indices.shape[0]
    index_array = np.zeros((rows, seq_length), dtype=int)
    for i in range(seq_length):
        index_array[:,i] = indices + 1 - seq_length + i
    uniques = np.unique(index_array.flatten())
    df.loc[uniques].to_csv('test_220_100k.csv',index_label='Index')
    np.savetxt('test_220_100k.indices',indices.astype(int),fmt='%d')

# create_test_sample(tdf, validate_indices[:100000]) # Uncomment this line to generate a test sample                    

[11386714 20819702 13959897 ...  7418203 13532884  5122780]


# Define custom mapping functions

In [10]:
def timeEncoder(X):
    X_hm = X['Time'].str.split(':', expand=True)
    d = pd.to_datetime(dict(year=X['Year'],month=X['Month'],day=X['Day'],hour=X_hm[0],minute=X_hm[1]))
    d = d.values.astype(int)
    print(d.dtype)
    d = d.astype(int)
    return pd.DataFrame(d)

def amtEncoder(X):
    amt = X.apply(lambda x: x[1:]).astype(float).map(lambda amt: max(1,amt)).map(math.log)
    return pd.DataFrame(amt)

def decimalEncoder(X,length=5):
    dnew = pd.DataFrame()
    for i in range(length):
        dnew[i] = np.mod(X,10) 
        X = np.floor_divide(X,10)
    return dnew

def fraudEncoder(X):
    return np.where(X == 'Yes', 1, 0).astype(int)

# Fit the whole data using DataFrameMapper and pickle the mapper

In [11]:
save_dir = 'saved_models/P/ccf_220_keras_gru_static/1'

In [12]:
from sklearn_pandas import DataFrameMapper
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import FunctionTransformer
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import LabelBinarizer
from sklearn.impute import SimpleImputer

mapper = DataFrameMapper([
                          ('Is Fraud?', FunctionTransformer(fraudEncoder)),
                          (['Merchant State'], [SimpleImputer(strategy='constant'), FunctionTransformer(np.ravel),
                                               LabelEncoder(), FunctionTransformer(decimalEncoder), OneHotEncoder()]),
                          (['Zip'], [SimpleImputer(strategy='constant'), FunctionTransformer(np.ravel),
                                     FunctionTransformer(decimalEncoder), OneHotEncoder()]),
                          ('Merchant Name', [LabelEncoder(), FunctionTransformer(decimalEncoder), OneHotEncoder()]),
                          ('Merchant City', [LabelEncoder(), FunctionTransformer(decimalEncoder), OneHotEncoder()]),
                          ('MCC', [LabelEncoder(), FunctionTransformer(decimalEncoder), OneHotEncoder()]),
                          (['Use Chip'], [SimpleImputer(strategy='constant'), LabelBinarizer()]),
                          (['Errors?'], [SimpleImputer(strategy='constant'), LabelBinarizer()]),
                          (['Year','Month','Day','Time'], [FunctionTransformer(timeEncoder), MinMaxScaler()]),
                          ('Amount', [FunctionTransformer(amtEncoder), MinMaxScaler()])
                         ], input_df=True, df_out=True)
mapper.fit(tdf)

joblib.dump(mapper, open('fitted_mapper.pkl','wb'))

int32


In [13]:
mapper = joblib.load(open('fitted_mapper.pkl','rb'))

# Do a transform on one row to get number of mapped features (including label)

In [14]:
mapped_sample = mapper.transform(tdf[:100])
mapped_size = mapped_sample.shape[-1]
print(mapped_size)

C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_fea

int32
221


# Generator for training batches

In [15]:
def gen_training_batch(df, mapper, index_list, batch_size):
    np.random.seed(98765)
    train_df = df.loc[index_list]
    non_fraud_indices = train_df[train_df['Is Fraud?'] == 'No'].index.values
    fraud_indices = train_df[train_df['Is Fraud?'] == 'Yes'].index.values
    fsize = fraud_indices.shape[0]
    while True:
        indices = np.concatenate((fraud_indices,np.random.choice(non_fraud_indices,fsize,replace=False)))
        np.random.shuffle(indices)
        rows = indices.shape[0]
        index_array = np.zeros((rows, seq_length), dtype=np.int)
        for i in range(seq_length):
            index_array[:,i] = indices + 1 - seq_length + i
        full_df = mapper.transform(df.loc[index_array.flatten()])
        target_buffer = full_df['Is Fraud?'].to_numpy().reshape(rows, seq_length, 1)
        data_buffer = full_df.drop(['Is Fraud?'],axis=1).to_numpy().reshape(rows, seq_length, -1)

        batch_ptr = 0
        while (batch_ptr + batch_size) <= rows:
            data = data_buffer[batch_ptr:batch_ptr+batch_size]
            targets = target_buffer[batch_ptr:batch_ptr+batch_size]
            batch_ptr += batch_size
            data_t = np.transpose(data, axes=(1,0,2))
            targets_t = np.transpose(targets, axes=(1,0,2))
            yield data_t,targets_t

# Utilities 

In [16]:
def print_trainable_parameters():
    total = 0
    for variable in tf.trainable_variables():
        shape = variable.get_shape()
        parameters = 1
        for dim in shape:
            parameters *= dim
        total += parameters
        print (variable, shape, parameters)
    print(total)

def f1(conf):
    precision = float(conf[1][1]) / (conf[1][1]+conf[0][1])
    recall = float(conf[1][1]) / (conf[1][1]+conf[1][0])
    return 2 * precision * recall / (precision + recall)

class TP(tf.keras.metrics.TruePositives):
    def update_state(self, y_true, y_pred, sample_weight=None):
        super().update_state(y_true[-1,:,:], y_pred[-1,:,:], sample_weight)

class FP(tf.keras.metrics.FalsePositives):
    def update_state(self, y_true, y_pred, sample_weight=None):
        super().update_state(y_true[-1,:,:], y_pred[-1,:,:], sample_weight)

class FN(tf.keras.metrics.FalseNegatives):
    def update_state(self, y_true, y_pred, sample_weight=None):
        super().update_state(y_true[-1,:,:], y_pred[-1,:,:], sample_weight)

class TN(tf.keras.metrics.TrueNegatives):
    def update_state(self, y_true, y_pred, sample_weight=None):
        super().update_state(y_true[-1,:,:], y_pred[-1,:,:], sample_weight)


# Graph parameters

In [17]:
units = [200,200]
input_size = mapped_size - 1
output_size = 1

In [18]:
!pip install graphviz

# Tensorflow graph construction

In [19]:
batch_size = 16
tf_input = ([batch_size, input_size])

gru_model = tf.keras.models.Sequential([
    tf.keras.layers.GRU(units[0], input_shape=tf_input, batch_size=7, time_major=True, return_sequences=True),
    tf.keras.layers.GRU(units[1], return_sequences=True, time_major=True),
    tf.keras.layers.Dense(output_size, activation='sigmoid')
])

gru_model.summary()
# from keras.utils.vis_utils import plot_model
tf.keras.utils.plot_model(gru_model, 'model.png', show_shapes=True)

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 gru (GRU)                   (7, 16, 200)              253200    
                                                                 
 gru_1 (GRU)                 (7, 16, 200)              241200    
                                                                 
 dense (Dense)               (7, 16, 1)                201       
                                                                 
Total params: 494,601
Trainable params: 494,601
Non-trainable params: 0
_________________________________________________________________
You must install pydot (`pip install pydot`) and install graphviz (see instructions at https://graphviz.gitlab.io/download/) for plot_model to work.


In [20]:
metrics=['accuracy', 
    TP(name='TP'),
    FP(name='FP'),
    FN(name='FN'),
    TN(name='TN'),
    tf.keras.metrics.TruePositives(name='tp'),
    tf.keras.metrics.FalsePositives(name='fp'),
    tf.keras.metrics.FalseNegatives(name='fn'),
    tf.keras.metrics.TrueNegatives(name='tn')
   ]

# Compile graph

In [21]:
gru_model.compile(optimizer='adam', loss='binary_crossentropy', metrics=metrics)

# Tensorflow training parameters

In [22]:
steps_per_epoch = 20000
checkpoint_dir = "./checkpoints/ccf_220_keras_gru_static/"
filepath = checkpoint_dir + "iter-{epoch:02d}/model.ckpt"
batch_size = 16

# Tensorflow training

In [23]:
print ("Learning...")
cp_callback = tf.keras.callbacks.ModelCheckpoint(filepath=filepath, save_weights_only=True, verbose=1)
train_generate = gen_training_batch(tdf,mapper,train_indices,batch_size)
gru_model.fit(train_generate, epochs=2, steps_per_epoch=steps_per_epoch, verbose=1, callbacks=[cp_callback])

Learning...


C:\Users\Administrator\AppData\Local\Temp\1\ipykernel_9512\3206109500.py:11: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_array = np.zeros((rows, seq_length), dtype=np.int)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.

int32
Epoch 1/2
 1859/50000 [>.............................] - ETA: 22:16 - loss: 0.1530 - accuracy: 0.9490 - TP: 12768.0000 - FP: 356.0000 - FN: 2103.0000 - TN: 14517.0000 - tp: 40911.0000 - fp: 2889.0000 - fn: 7728.0000 - tn: 156680.0000

C:\Users\Administrator\AppData\Local\Temp\1\ipykernel_9512\3206109500.py:11: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_array = np.zeros((rows, seq_length), dtype=np.int)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.

int32
 3717/50000 [=>............................] - ETA: 26:01 - loss: 0.1303 - accuracy: 0.9560 - TP: 26277.0000 - FP: 674.0000 - FN: 3454.0000 - TN: 29067.0000 - tp: 83838.0000 - fp: 4886.0000 - fn: 13417.0000 - tn: 314163.0000

...

int32
46668/50000 [===========================>..] - ETA: 2:38 - loss: 0.0085 - accuracy: 0.9970 - TP: 372649.0000 - FP: 804.0000 - FN: 701.0000 - TN: 372534.0000 - tp: 1212300.0000 - fp: 6310.0000 - fn: 9509.0000 - tn: 3998697.0000

C:\Users\Administrator\AppData\Local\Temp\1\ipykernel_9512\3206109500.py:11: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_array = np.zeros((rows, seq_length), dtype=np.int)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.

int32
48527/50000 [============================>.] - ETA: 1:10 - loss: 0.0084 - accuracy: 0.9970 - TP: 387493.0000 - FP: 826.0000 - FN: 730.0000 - TN: 387383.0000 - tp: 1260606.0000 - fp: 6519.0000 - fn: 9856.0000 - tn: 4158043.0000

C:\Users\Administrator\AppData\Local\Temp\1\ipykernel_9512\3206109500.py:11: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_array = np.zeros((rows, seq_length), dtype=np.int)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.

int32
50000/50000 [==============================] - ETA: 0s - loss: 0.0084 - accuracy: 0.9970 - TP: 399234.0000 - FP: 850.0000 - FN: 746.0000 - TN: 399170.0000 - tp: 1298775.0000 - fp: 6691.0000 - fn: 10120.0000 - tn: 4284414.0000
Epoch 2: saving model to ./checkpoints/ccf_220_keras_gru_static/iter-02\model.ckpt
50000/50000 [==============================] - 2402s 48ms/step - loss: 0.0084 - accuracy: 0.9970 - TP: 399234.0000 - FP: 850.0000 - FN: 746.0000 - TN: 399170.0000 - tp: 1298775.0000 - fp: 6691.0000 - fn: 10120.0000 - tn: 4284414.0000


# Save model from checkpoint

In [24]:
gru_model.save_weights(os.path.join(save_dir,"wts"))
gru_model.save(save_dir)

INFO:tensorflow:Assets written to: saved_models/P/ccf_220_keras_gru_static/1\assets


INFO:tensorflow:Assets written to: saved_models/P/ccf_220_keras_gru_static/1\assets


# Generator for validation/test batches

In [25]:
def gen_test_batch(df, mapper, indices, batch_size):
    rows = indices.shape[0]
    index_array = np.zeros((rows, seq_length), dtype=np.int)
    for i in range(seq_length):
        index_array[:,i] = indices + 1 - seq_length + i
    count = 0
    while (count + batch_size <= rows):        
        full_df = mapper.transform(df.loc[index_array[count:count+batch_size].flatten()])
        data = full_df.drop(['Is Fraud?'],axis=1).to_numpy().reshape(batch_size, seq_length, -1)
        targets = full_df['Is Fraud?'].to_numpy().reshape(batch_size, seq_length, 1)
        count += batch_size
        data_t = np.transpose(data, axes=(1,0,2))
        targets_t = np.transpose(targets, axes=(1,0,2))
        yield data_t, targets_t

# Tensorflow test

In [26]:
batch_size = 2000

input_size=220
output_size=1
units=[200,200]

tf_input = ([batch_size, input_size])

new_model = tf.keras.models.Sequential([
    tf.keras.layers.GRU(units[0], input_shape=tf_input, batch_size=7, time_major=True, return_sequences=True),
    tf.keras.layers.GRU(units[1], return_sequences=True, time_major=True),
    tf.keras.layers.Dense(output_size, activation='sigmoid')
])
new_model.load_weights(os.path.join(save_dir,"wts"))
new_model.compile(optimizer='adam', loss='binary_crossentropy', metrics=metrics)
ddf = pd.read_csv('test_220_100k.csv', dtype={"Merchant Name":"str"}, index_col='Index')
indices = np.loadtxt('test_220_100k.indices')

batch_size = 2000

print("\nQuick test")
test_generate = gen_test_batch(ddf,mapper,indices,batch_size)
new_model.evaluate(test_generate, verbose=1)

print("\nFull test")
test_generate = gen_test_batch(tdf,mapper,test_indices,batch_size)
new_model.evaluate(test_generate, verbose=1)


Quick test


C:\Users\Administrator\AppData\Local\Temp\1\ipykernel_9512\4121024059.py:3: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_array = np.zeros((rows, seq_length), dtype=np.int)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.p

int32


C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


      1/Unknown - 4s 4s/step - loss: 0.0058 - accuracy: 0.9984 - TP: 399235.0000 - FP: 852.0000 - FN: 746.0000 - TN: 401167.0000 - tp: 1298788.0000 - fp: 6714.0000 - fn: 10120.0000 - tn: 4298378.0000

...

C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


   2434/Unknown - 5723s 2s/step - loss: 0.0065 - accuracy: 0.9984 - TP: 5622.0000 - FP: 8294.0000 - FN: 327.0000 - TN: 4853757.0000 - tp: 37110.0000 - fp: 51564.0000 - fn: 4340.0000 - tn: 33983000.0000

C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\Administrator\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


int32
2435/2435 [==============================] - 5726s 2s/step - loss: 0.0065 - accuracy: 0.9984 - TP: 5622.0000 - FP: 8295.0000 - FN: 327.0000 - TN: 4855756.0000 - tp: 37110.0000 - fp: 51580.0000 - fn: 4340.0000 - tn: 33996984.0000


[0.006460787728428841,
 0.9983598589897156,
 5622.0,
 8295.0,
 327.0,
 4855756.0,
 37110.0,
 51580.0,
 4340.0,
 33996984.0]

In [27]:
import json
metrics = {"metrics": new_model.metrics_names}
metrics = json.dumps(metrics)
with open("metrcs.json", "w") as outfile:
    outfile.write(metrics)

def f1(conf):
    precision = float(conf[1][1]) / (conf[1][1]+conf[0][1])
    recall = float(conf[1][1]) / (conf[1][1]+conf[1][0])
    return 2 * precision * recall / (precision + recall)

In [28]:
print(f1([[99710,172],[6,112]]))
print(f1([[4855814,8237],[381,5568]]))

0.5572139303482587
0.563733927305862


In [29]:
batch_size = 16
tf_input = ([batch_size, input_size])

new_model = tf.keras.models.Sequential([
    tf.keras.layers.GRU(units[0], input_shape=tf_input, batch_size=7, time_major=True, return_sequences=True),
    tf.keras.layers.GRU(units[1], return_sequences=True, time_major=True),
    tf.keras.layers.Dense(output_size, activation='sigmoid')
])
new_model.load_weights(os.path.join(save_dir,"wts"))
new_model.compile(optimizer='adam', loss='binary_crossentropy')

In [32]:
new_model.summary()
from keras.utils.vis_utils import plot_model
plot_model(new_model, 'model2.png', show_shapes=True, expand_nested=True)

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 gru_4 (GRU)                 (7, 16, 200)              253200    
                                                                 
 gru_5 (GRU)                 (7, 16, 200)              241200    
                                                                 
 dense_2 (Dense)             (7, 16, 1)                201       
                                                                 
Total params: 494,601
Trainable params: 494,601
Non-trainable params: 0
_________________________________________________________________
You must install pydot (`pip install pydot`) and install graphviz (see instructions at https://graphviz.gitlab.io/download/) for plot_model to work.


In [33]:
# pip install keras2onnx
pip install onnx


     ---------------------------------------- 96.3/96.3 kB 1.1 MB/s eta 0:00:00
     ---------------------------------------- 83.8/83.8 kB 1.2 MB/s eta 0:00:00
     ---------------------------------------- 88.3/88.3 kB 2.5 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
     --------------------------------------- 12.2/12.2 MB 25.2 MB/s eta 0:00:00
     -------------------------------------- 904.2/904.2 kB 5.2 MB/s eta 0:00:00
  Created wheel for fire: filename=fire-0.5.0-py2.py3-none-any.whl size=116933 sha256=d188cee0113572d97b808b50eecf4fa609a188aa4498a6eb3ba4938b24aa870c
  Stored in directory: c:\users\administrator\appdata\local\pip\cache\wheels\f7\f1\89\b9ea2bf8f80ec027a88fef1d354b3816b4d3d29530988972f6
Successfully built fire
  Attempting uninstall: protobuf
    Found existing installation: protobuf 3.19.6
    Uninstalling protobuf-3.19.6:
      Successfully uninstalled protobuf-3.19.6


ERROR: Could not install packages due to an OSError: [WinError 5] Access is denied: 'C:\\Users\\Administrator\\Anaconda3\\Lib\\site-packages\\google\\~rotobuf\\internal\\_api_implementation.cp39-win_amd64.pyd'
Consider using the `--user` option or check the permissions.



## Convert to onnx

In [31]:

from tensorflow import keras
import keras2onnx
import onnx

# convert to onnx
onnx_model = keras2onnx.convert_keras(new_model, new_model.name)

# Save
onnx.save_model(onnx_model, "ccf_gru_static_keras2onnx.onnx")

ModuleNotFoundError: No module named 'keras2onnx'

In [ ]:
import tf2onnx

# convert to onnx
spec = (tf.TensorSpec((7, 16, 220), tf.float32, name="input"),)
output_path = new_model.name + ".onnx"

onnx_model = tf2onnx.convert.from_keras(new_model, spec, output_path=output_path)